<a href="https://colab.research.google.com/github/anespart1/work_automation_use/blob/main/CSV_to_JSON_Visualization.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#Python code for changing CSV format to JSON and visualization

In [ ]:
from google.colab import drive, files
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
#-*- coding:cp949 -*-
import folium
import urllib
import json
import pandas as pd
import ast
import os
import folium.plugins
print(folium.__version__)

0.8.3


In [ ]:
df = pd.read_csv('/content/drive/MyDrive/Colab Notebooks/17_20_lg.csv', encoding='cp949')
df.head(1)

사고다발지FID  사고다발지ID     법정동코드      지점코드      시도시군구명  \
0   6467416  2018074  11110174  11110001  서울특별시 종로구1   

                        지점명  사고건수  사상자수  사망자수  중상자수  경상자수  부상신고자수          경도  \
0  서울특별시 종로구 창신동(동대문로터리 인근)    42    69     1    12    48       8  127.009055   

          위도                                            다발지역폴리곤  
0  37.571348  {"type":"Polygon","coordinates":[[[127.0104026...

In [ ]:
print(df['다발지역폴리곤'][0])
type(df['다발지역폴리곤'][0])

{"type":"Polygon","coordinates":[[[127.01040263,37.57134779],[127.01037674,37.57113943],[127.01030006,37.57093908],[127.01017554,37.57075444],[127.01000797,37.57059259],[127.00980378,37.57045977],[127.00957082,37.57036108],[127.00931804,37.5703003],[127.00905516,37.57027978],[127.00879228,37.5703003],[127.00853951,37.57036108],[127.00830655,37.57045977],[127.00810235,37.57059259],[127.00793478,37.57075444],[127.00781026,37.57093908],[127.00773358,37.57113943],[127.00770769,37.57134779],[127.00773358,37.57155614],[127.00781026,37.57175649],[127.00793478,37.57194113],[127.00810235,37.57210297],[127.00830655,37.57223579],[127.00853951,37.57233448],[127.00879228,37.57239526],[127.00905516,37.57241578],[127.00931804,37.57239526],[127.00957082,37.57233448],[127.00980378,37.57223579],[127.01000797,37.57210297],[127.01017554,37.57194113],[127.01030006,37.57175649],[127.01037674,37.57155614],[127.01040263,37.57134779]]]}


str

In [ ]:
#df['다발지역폴리곤']의 데이터 구조
#{ "type":"Polygon",
#  "coordinates":[[[y0, x0]...[yn, xn]]] }

#단일 GeoJSON 구조
#{'geometry': {'coordinates': [[[y0, x0]...[yn, xn]]],
#  'type': 'Polygon'},
# 'properties': {'base_year': '2013',
#                ...
#                'name_eng': 'Gangdong-gu'},
# 'type': 'Feature'}

#복수 이상의 GeoJSON 구조
#[
#  {'geometry': {'coordinates': [[[y0, x0]...[yn, xn]]],
#   'type': 'Polygon'},
#  'properties': {'base_year': '2013',
#   'code': '11250',
#   'name': '강동구',
#   'name_eng': 'Gangdong-gu'},
#  'type': 'Feature'},
#
# {'geometry': {'coordinates': [[[y0, x0]...[yn, xn]]],
#   'type': 'Polygon'},
#  'properties': {'base_year': '2013',
#   'code': '11240',
#   'name': '송파구',
#   'name_eng': 'Songpa-gu'},
#  'type': 'Feature'}
#  ]

In [ ]:
df.head(1)

사고다발지FID  사고다발지ID     법정동코드      지점코드      시도시군구명  \
0   6467416  2018074  11110174  11110001  서울특별시 종로구1   

                        지점명  사고건수  사상자수  사망자수  중상자수  경상자수  부상신고자수          경도  \
0  서울특별시 종로구 창신동(동대문로터리 인근)    42    69     1    12    48       8  127.009055   

          위도                                            다발지역폴리곤  
0  37.571348  {"type":"Polygon","coordinates":[[[127.0104026...

In [ ]:
#속성정보값 자동 입력코드
def make_properties(dafaframe=None):
  properties = []
  for i in range(len(df)):
    totalc = []
    for j in range(len(df.columns[:-1])):
      if type(df[df.columns[j]][i]) == str:
        ptxt = '"{}":"{}"'.format(df.columns[j], df[df.columns[j]][i])
      else:
        ptxt = '"{}":{}'.format(df.columns[j], df[df.columns[j]][i])
      totalc.append(ptxt)
    totalc = '{' + ','.join(totalc) + '}'
    properties.append(totalc)
  return properties

In [ ]:
properties = make_properties(df)
properties[0]

'{"사고다발지FID":6467416,"사고다발지ID":2018074,"법정동코드":11110174,"지점코드":11110001,"시도시군구명":"서울특별시 종로구1","지점명":"서울특별시 종로구 창신동(동대문로터리 인근)","사고건수":42,"사상자수":69,"사망자수":1,"중상자수":12,"경상자수":48,"부상신고자수":8,"경도":127.0090552,"위도":37.57134779}'

In [ ]:
objtxts = []
for i in range(len(df)):
  objtxt = '{"type":"Feature", "geometry":' + df['다발지역폴리곤'][i] + ',"properties":' + properties[i] + '}'
  objtxts.append(objtxt)
objtxts[0]

'{"type":"Feature", "geometry":{"type":"Polygon","coordinates":[[[127.01040263,37.57134779],[127.01037674,37.57113943],[127.01030006,37.57093908],[127.01017554,37.57075444],[127.01000797,37.57059259],[127.00980378,37.57045977],[127.00957082,37.57036108],[127.00931804,37.5703003],[127.00905516,37.57027978],[127.00879228,37.5703003],[127.00853951,37.57036108],[127.00830655,37.57045977],[127.00810235,37.57059259],[127.00793478,37.57075444],[127.00781026,37.57093908],[127.00773358,37.57113943],[127.00770769,37.57134779],[127.00773358,37.57155614],[127.00781026,37.57175649],[127.00793478,37.57194113],[127.00810235,37.57210297],[127.00830655,37.57223579],[127.00853951,37.57233448],[127.00879228,37.57239526],[127.00905516,37.57241578],[127.00931804,37.57239526],[127.00957082,37.57233448],[127.00980378,37.57223579],[127.01000797,37.57210297],[127.01017554,37.57194113],[127.01030006,37.57175649],[127.01037674,37.57155614],[127.01040263,37.57134779]]]},"properties":{"사고다발지FID":6467416,"사고다발지ID":

In [ ]:
dicts = '{"type":"FeatureCollection","features":[' + ','.join(objtxts) + ']}'

In [ ]:
#지도 타일 종류 추가
m = folium.Map(
    location=[37.559819, 126.963895],
    zoom_start=11,
    control_scale = True)

for i in ['Stamen Terrain', 'Stamen Water Color', 'cartodbpositron']:
  folium.TileLayer(i).add_to(m)

sago = ast.literal_eval(dicts)

folium.GeoJson(sago,
               name='사고다발지역').add_to(m)

#Heatmap 추가
heatmap = folium.plugins.HeatMap(zip(df[df.columns[13]].values.tolist(), df[df.columns[12]].values.tolist()),
                                 name='Density', radius=22, min_opacity=0.28)
m.add_child(heatmap)

#미니맵 추가
minimap = folium.plugins.MiniMap()
m.add_child(minimap)

#거리측량기 추가
m.add_child(folium.plugins.MeasureControl())

#좌표기 추가
folium.plugins.MousePosition(prefix='경위도 좌표:').add_to(m)

#전체화면모드 추가
folium.plugins.Fullscreen(title='전체화면',
                          title_cancel='돌아가기',
                          force_separate_button=True).add_to(m)

#레이어 컨트롤러 추가
folium.LayerControl().add_to(m)
m

In [ ]:
os.mkdir('/content/sago/')
m.save('/content/sago/map.html')
with open('/content/sago/사고다발지역.json', 'w', encoding='utf-8') as f:
    json.dump(sago, f, ensure_ascii=False, indent=4)
!zip -r /content/사고다발지역.zip /content/sago/
files.download('/content/사고다발지역.zip')

  adding: content/sago/ (stored 0%)
  adding: content/sago/map.html (deflated 83%)
  adding: content/sago/사고다발지역.json (deflated 94%)


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>